# GeoHackathon Data Analysis Notebook

### Introduction

This Jupyter Notebook is created for the 2024 SPE Europe Energy GeoHackathon. The main objective is to analyze well and seismic data from Croatia and use machine learning techniques to predict reservoir properties for two new wells. This is essential for planning the development of a geothermal field that will generate electricity for a town of 50,000 people.

The challenge is divided into two parts:

1. **Data Analysis and Machine Learning Task (60%)**:
   - Review and preprocess data from 6 existing wells and seismic data.
   - Train a machine learning model to predict reservoir properties for two new wells (wells 7 and 8).

2. **Geothermal Development Plan (40%)**:
   - Using the predicted properties, create a field development plan including the number of wells, production estimation, electricity generation capacity, and economic feasibility.

The dataset includes:
- Well data (depth, temperature, coordinates, etc.)
- Seismic data for correlating subsurface features

In this notebook, we will go through:
1. Data loading and review
2. Data preprocessing and cleaning
3. Exploratory data analysis
4. Feature engineering
5. Machine learning model training and evaluation
6. Saving the trained model

The properties to predict are the permeability, porosity and temperature.

# 2. Well data

## 2.1 Official files

In [1]:
# Install the necessary libraries
%pip install lasio pandas missingno

# Import the libraries 
import os
import pandas as pd
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import plotly.graph_objects as go
import plotly.express as px
from ipywidgets import interact, Dropdown
import missingno as msno

## 1. WELL DATA - OFFICIAL FILES 

# Base path for well data
official_files_path = r".\Data\Wells\Official Files"

# Load the different CSV files
collar_file = os.path.join(official_files_path, "Wells_Collar.csv")
geology_file = os.path.join(official_files_path, "Wells_Geology.csv")
geology_strat_simpl_file = os.path.join(official_files_path, "Wells_Geology_StratSimpl.csv")
las_points_file = os.path.join(official_files_path, "Wells_LAS_Points.csv")
survey_dip_file = os.path.join(official_files_path, "Wells_Survey_Dip.csv")

# Read the CSV files into Pandas DataFrames
collar_df = pd.read_csv(collar_file)
geology_df = pd.read_csv(geology_file, encoding='latin1')
geology_strat_simpl_df = pd.read_csv(geology_strat_simpl_file)
las_points_df = pd.read_csv(las_points_file)
survey_dip_df = pd.read_csv(survey_dip_file)

# Create a table summarizing the LAS dataset
las_summary = pd.DataFrame({
    'Variable': [
        'AC', 'CAL', 'CN', 'DEN', 'depth', 'GR', 'holeid', 'PERM', 'PF', 'POR',
        'PORT', 'PORW', 'R16', 'R64', 'RD', 'RLML', 'RNML', 'SP', 'TEMP'
    ],
    'Description': [
        'Acoustic log (travel time)',
        'Caliper log (borehole diameter)',
        'Compensated Neutron log (neutron porosity)',
        'Bulk Density (g/cc)',
        'Depth of measurement in meters',
        'Gamma Ray (API units)',
        'Well identifier',
        'Permeability (mD)',
        'Formation factor (resistivity factor)',
        'Porosity (%)',
        'Total porosity (%)',
        'Water-filled porosity (%)',
        'Resistivity at 16 inches (ohm-m)',
        'Resistivity at 64 inches (ohm-m)',
        'Deep resistivity (ohm-m)',
        'Laterolog medium resistivity (ohm-m)',
        'Neutron-medium resistivity (ohm-m)',
        'Spontaneous Potential (mV)', 
        'Temperature (°C)'
    ]
})

# Visualize the summary in a table
fig = go.Figure(data=[go.Table(
    header=dict(values=['Variable', 'Description'],
                fill_color='paleturquoise',
                align='left'),
    cells=dict(values=[las_summary['Variable'], las_summary['Description']],
               fill_color='lavender',
               align='left')
)])
fig.update_layout(title='Summary of LAS Dataset')
fig.show()

# Fig 1. Interactive plot of missing data for each variable in the LAS dataset
def plot_missing_data():
    msno.matrix(las_points_df)
    plt.title('Missing Data Overview for LAS Points Dataset')
    plt.show()

# Create an interactive widget to visualize missing data
interact(plot_missing_data)

# Fig 2. Interactive plot of missing data for each well in the LAS dataset
def plot_missing_data(holeid):
    filtered_df = las_points_df[las_points_df['holeid'] == holeid]
    msno.matrix(filtered_df)
    plt.title(f'Missing Data Overview for Well: {holeid}')
    plt.show()

# Create an interactive widget to visualize missing data by well
interact(plot_missing_data, holeid=Dropdown(options=las_points_df['holeid'].unique(), description='Well ID:'))

# Fig 3. Visualize simplified stratigraphy for each well with bars representing formations (interactive)
formations = geology_strat_simpl_df['Strat_Simplified_Viro'].unique()
colors = plt.cm.get_cmap('tab20', len(formations))

fig = go.Figure()
for idx, well_id in enumerate(geology_strat_simpl_df['WellID'].unique()):
    well_strat = geology_strat_simpl_df[geology_strat_simpl_df['WellID'] == well_id]
    for _, row in well_strat.iterrows():
        color_index = list(formations).index(row['Strat_Simplified_Viro'])
        fig.add_trace(go.Bar(
            x=[row['To'] - row['From']],
            y=[well_id],
            base=row['From'],
            orientation='h',
            marker=dict(color=f'rgba({colors(color_index)[0]*255},{colors(color_index)[1]*255},{colors(color_index)[2]*255},1.0)'),
            name=row['Strat_Simplified_Viro']
        ))

fig.update_layout(
    xaxis_title='Depth (m)',
    yaxis_title='Well ID',
    title='Simplified Stratigraphy for Wells (Interactive)',
    barmode='stack',
    showlegend=True
)
fig.show()

# Fig 4. Visualize simplified stratigraphy for each well with bars representing formations (interactive)
formations = geology_strat_simpl_df['Strat_Simplified'].unique()
colors = plt.cm.get_cmap('tab20', len(formations))

fig = go.Figure()
for idx, well_id in enumerate(geology_strat_simpl_df['WellID'].unique()):
    well_strat = geology_strat_simpl_df[geology_strat_simpl_df['WellID'] == well_id]
    for _, row in well_strat.iterrows():
        color_index = list(formations).index(row['Strat_Simplified'])
        fig.add_trace(go.Bar(
            x=[row['To'] - row['From']],
            y=[well_id],
            base=row['From'],
            orientation='h',
            marker=dict(color=f'rgba({colors(color_index)[0]*255},{colors(color_index)[1]*255},{colors(color_index)[2]*255},1.0)'),
            name=row['Strat_Simplified']
        ))

fig.update_layout(
    xaxis_title='Depth (m)',
    yaxis_title='Well ID',
    title='Simplified Stratigraphy for Wells (Interactive)',
    barmode='stack',
    showlegend=True
)
fig.show()

# Fig 5. Visualize stratigraphy for each well with bars representing formations (interactive)
formations = geology_df['Stratigraphy'].unique()
colors = plt.cm.get_cmap('tab20', len(formations))

fig = go.Figure()
for idx, well_id in enumerate(geology_df['WellID'].unique()):
    well_strat = geology_df[geology_df['WellID'] == well_id]
    for _, row in well_strat.iterrows():
        color_index = list(formations).index(row['Stratigraphy'])
        fig.add_trace(go.Bar(
            x=[row['To'] - row['From']],
            y=[well_id],
            base=row['From'],
            orientation='h',
            marker=dict(color=f'rgba({colors(color_index)[0]*255},{colors(color_index)[1]*255},{colors(color_index)[2]*255},1.0)'),
            name=row['Stratigraphy']
        ))

fig.update_layout(
    xaxis_title='Depth (m)',
    yaxis_title='Well ID',
    title='Stratigraphy for Wells (Interactive)',
    barmode='stack',
    showlegend=True
)
fig.show()

# Fig 6. 3D version of the simplified stratigraphy with X_UTM and Y_UTM, with well names displayed once, without markers
fig = go.Figure()
formations = geology_strat_simpl_df['Strat_Simplified_Viro'].unique()
colors = plt.cm.get_cmap('tab20', len(formations))

for well_id in geology_strat_simpl_df['WellID'].unique():
    well_strat = geology_strat_simpl_df[geology_strat_simpl_df['WellID'] == well_id]
    collar_info = collar_df[collar_df['Name'] == well_id].iloc[-1]
    x_coord = collar_info['X_UTM']
    y_coord = collar_info['Y_UTM']
    
    first_trace = True
    for _, row in well_strat.iterrows():
        color_index = list(formations).index(row['Strat_Simplified_Viro'])
        fig.add_trace(go.Scatter3d(
            x=[x_coord, x_coord],
            y=[y_coord, y_coord],
            z=[- row['From'], - row['To']],
            mode='lines+text' if first_trace else 'lines',
            line=dict(color=f'rgba({colors(color_index)[0]*255},{colors(color_index)[1]*255},{colors(color_index)[2]*255},1.0)', width=10),
            text=[well_id, ''] if first_trace else ['', ''],
            textposition='top right',
            name=f'{well_id} - {row["Strat_Simplified_Viro"]}'
        ))
        first_trace = False

fig.update_layout(
    scene=dict(
        xaxis_title='X Coordinate (UTM)',
        yaxis_title='Y Coordinate (UTM)',
        zaxis_title='Depth (m)',
    ),
    title='3D Simplified Stratigraphy for Wells with Well Names',
    showlegend=True
)
fig.show()

# Fig 7. 3D version of the stratigraphy with X_UTM and Y_UTM, with well names displayed once, without markers
fig = go.Figure()
formations = geology_df['Stratigraphy'].unique()
colors = plt.cm.get_cmap('tab20', len(formations))

for well_id in geology_df['WellID'].unique():
    well_strat = geology_df[geology_df['WellID'] == well_id]
    collar_info = collar_df[collar_df['Name'] == well_id].iloc[-1]
    x_coord = collar_info['X_UTM']
    y_coord = collar_info['Y_UTM']
    
    first_trace = True
    for _, row in well_strat.iterrows():
        color_index = list(formations).index(row['Stratigraphy'])
        fig.add_trace(go.Scatter3d(
            x=[x_coord, x_coord],
            y=[y_coord, y_coord],
            z=[- row['From'], - row['To']],
            mode='lines+text' if first_trace else 'lines',
            line=dict(color=f'rgba({colors(color_index)[0]*255},{colors(color_index)[1]*255},{colors(color_index)[2]*255},1.0)', width=10),
            text=[well_id, ''] if first_trace else ['', ''],
            textposition='top right',
            name=f'{well_id} - {row["Stratigraphy"]}'
        ))
        first_trace = False

fig.update_layout(
    scene=dict(
        xaxis_title='X Coordinate (UTM)',
        yaxis_title='Y Coordinate (UTM)',
        zaxis_title='Depth (m)',
    ),
    title='3D Stratigraphy for Wells with Well Names',
    showlegend=True
)
fig.show()

# Fig 8. Interactive visualization of porosity profiles and other LAS variables
variables = las_points_df.columns.tolist()
variables.remove('holeid')  # Remove the well identifier column
variables.remove('depth')  # Remove the depth column as it will be the x-axis

def plot_las_variable(variable):
    fig = px.line(
        las_points_df,
        x='depth',
        y=variable,
        color='holeid',
        title=f'Profiles of {variable} for Wells',
        labels={
            'depth': 'Depth (m)',
            variable: variable,
            'holeid': 'Well Name'
        }
    )
    fig.update_layout(
        xaxis_title='Depth (m)',
        yaxis_title=variable,
        legend_title='Well Name'
    )
    fig.show()

# Create an interactive widget to select which variable to plot
interact(plot_las_variable, variable=Dropdown(options=variables, description='Variable:'))




Defaulting to user installation because normal site-packages is not writeable
Note: you may need to restart the kernel to use updated packages.



[notice] A new release of pip is available: 24.2 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


interactive(children=(Output(),), _dom_classes=('widget-interact',))

interactive(children=(Dropdown(description='Well ID:', options=('LONCCARICA-1', 'REZOVACCKE_KRCCEVINE-1', 'REZ…

C:\Users\VX6595\AppData\Local\Temp\ipykernel_8880\2383530927.py:95: MatplotlibDeprecationWarning:

The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.



...

C:\Users\VX6595\AppData\Local\Temp\ipykernel_8880\2383530927.py:149: MatplotlibDeprecationWarning:

The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.



C:\Users\VX6595\AppData\Local\Temp\ipykernel_8880\2383530927.py:177: MatplotlibDeprecationWarning:

The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.



C:\Users\VX6595\AppData\Local\Temp\ipykernel_8880\2383530927.py:214: MatplotlibDeprecationWarning:

The get_cmap function was deprecated in Matplotlib 3.7 and will be removed in 3.11. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap()`` or ``pyplot.get_cmap()`` instead.



interactive(children=(Dropdown(description='Variable:', options=('AC', 'CAL', 'CN', 'DEN', 'GR', 'PERM', 'PF',…

<function __main__.plot_las_variable(variable)>

#### Observations
- Wells are all vertical (90°C DIP)
- Viro 1 litholohy wrongly evaluated ? Or just very different
- Need to concatenate and rename data (deptt, wellname)
- Need to clean some data + denoise
- Inference at this stage ?

In [2]:
# Generate Streamlit app & Deploy on web

# pip install streamlit
# streamlit run streamlit_app.py

# 2. Contatenate & clean data


In [5]:
import os
import pandas as pd
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D
import plotly.graph_objects as go
import plotly.express as px
from ipywidgets import interact, Dropdown
import missingno as msno

# Base path for well data
official_files_path = r".\Data\Wells\Official Files"

# Load the different CSV files
collar_file = os.path.join(official_files_path, "Wells_Collar.csv")
geology_file = os.path.join(official_files_path, "Wells_Geology.csv")
geology_strat_simpl_file = os.path.join(official_files_path, "Wells_Geology_StratSimpl.csv")
las_points_file = os.path.join(official_files_path, "Wells_LAS_Points.csv")
survey_dip_file = os.path.join(official_files_path, "Wells_Survey_Dip.csv")

# Read the CSV files into Pandas DataFrames
collar_df = pd.read_csv(collar_file)
geology_df = pd.read_csv(geology_file, encoding='latin1')
geology_strat_simpl_df = pd.read_csv(geology_strat_simpl_file)
las_points_df = pd.read_csv(las_points_file)
survey_dip_df = pd.read_csv(survey_dip_file)

# Convert WellID columns to string to ensure consistent data type across all DataFrames
collar_df['WellID'] = collar_df['Name'].astype(str)
geology_strat_simpl_df['WellID'] = geology_strat_simpl_df['WellID'].astype(str)
las_points_df['WellID'] = las_points_df['holeid'].astype(str)

# Rename and convert depth-related columns to float for consistent merging
las_points_df['Depth'] = las_points_df['depth'].astype(float)  # Rename depth to Depth
geology_strat_simpl_df['From'] = geology_strat_simpl_df['From'].astype(float)
collar_df = collar_df.rename(columns={'X_UTM': 'X', 'Y_UTM': 'Y', 'Z': 'Z'})

# Add TD, X, Y, Z from collar_df to las_points_df by merging on WellID
las_points_df = las_points_df.merge(collar_df[['WellID', 'TD', 'X_UTM', 'Y_UTM', 'Z']], on='WellID', how='left')

# Add stratigraphy information from geology_strat_simpl_df to las_points_df
# Match WellID and ensure Depth is within the range specified by 'From' and 'To'
las_points_df = pd.merge_asof(
    las_points_df.sort_values(by='Depth'),
    geology_strat_simpl_df.sort_values(by='From'),
    by='WellID',
    left_on='Depth',
    right_on='From',
    direction='backward'
)

# Display a preview of the concatenated data
print("\nConcatenated LAS Points Data:")
print(las_points_df.head())

# Create a table summarizing the LAS dataset
las_summary = pd.DataFrame({
    'Variable': [
        'AC', 'CAL', 'CN', 'DEN', 'Depth', 'GR', 'WellID', 'PERM', 'PF', 'POR',
        'PORT', 'PORW', 'R16', 'R64', 'RD', 'RLML', 'RNML', 'SP', 'TEMP', 'TD', 'X', 'Y', 'Z'
    ],
    'Description': [
        'Acoustic log (travel time)',
        'Caliper log (borehole diameter)',
        'Compensated Neutron log (neutron porosity)',
        'Bulk Density (g/cc)',
        'Depth of measurement in meters',
        'Gamma Ray (API units)',
        'Well identifier',
        'Permeability (mD)',
        'Formation factor (resistivity factor)',
        'Porosity (%)',
        'Total porosity (%)',
        'Water-filled porosity (%)',
        'Resistivity at 16 inches (ohm-m)',
        'Resistivity at 64 inches (ohm-m)',
        'Deep resistivity (ohm-m)',
        'Laterolog medium resistivity (ohm-m)',
        'Neutron-medium resistivity (ohm-m)',
        'Spontaneous Potential (mV)',
        'Temperature (°C)',
        'Total Depth (TD) of the well',
        'X Coordinate (UTM)',
        'Y Coordinate (UTM)',
        'Z Coordinate (elevation)'
    ],
    'Potential Utility for Project': [
        'Useful for identifying lithology and estimating rock properties such as porosity.',
        'Helps to assess borehole conditions and determine borehole stability.',
        'Used for evaluating porosity, particularly in limestone and dolomite formations.',
        'Helps to determine the bulk density of formations, crucial for estimating porosity and identifying lithology.',
        'Indicates the depth at which each measurement is taken, serving as a reference for all other logs.',
        'Useful for differentiating between shale and non-shale formations.',
        'Identifies the well being analyzed, essential for cross-referencing data.',
        'Crucial for assessing the ability of a rock to transmit fluids, important for reservoir quality evaluation.',
        'Helps to determine the resistivity properties and infer fluid saturation.',
        'Direct measurement of porosity, important for estimating the storage capacity of the reservoir.',
        'Total porosity gives a comprehensive view of the porosity, including both effective and ineffective portions.',
        'Useful for estimating the proportion of pore space filled with water, aiding in fluid distribution analysis.',
        'Shallow resistivity log that helps detect thin beds and fluid content near the borehole.',
        'Medium-depth resistivity log for determining fluid content and formation properties.',
        'Deep resistivity used to estimate hydrocarbon saturation and fluid distribution in deeper formations.',
        'Provides medium resistivity data that can help characterize reservoir rock properties.',
        'Provides neutron-related resistivity data, which helps in identifying gas zones.',
        'Used to determine formation potential, aiding in distinguishing lithologies and fluid types.',
        'Important for evaluating thermal gradients and understanding fluid properties in the formation.',
        'Depth of the well to understand the full extent of the drilling and possible reach of fluids.',
        'Provides spatial positioning of the well in the UTM coordinate system, used for mapping and visualization.',
        'Provides spatial positioning of the well in the UTM coordinate system, used for mapping and visualization.',
        'Elevation of the well site, useful for correcting measurements and understanding topography.'
    ]
})
print("\nSummary of LAS dataset:")
print(las_summary)

# Visualize the summary in a table
fig = go.Figure(data=[go.Table(
    header=dict(values=['Variable', 'Description', 'Potential Utility for Project'],
                fill_color='paleturquoise',
                align='left'),
    cells=dict(values=[las_summary['Variable'], las_summary['Description'], las_summary['Potential Utility for Project']],
               fill_color='lavender',
               align='left')
)])
fig.update_layout(title='Summary of LAS Dataset')
fig.show()

# Interactive plot of missing data for each well in the LAS dataset
def plot_missing_data(holeid):
    filtered_df = las_points_df[las_points_df['WellID'] == holeid]
    msno.matrix(filtered_df)
    plt.title(f'Missing Data Overview for Well: {holeid}')
    plt.show()

# Create an interactive widget to visualize missing data by well
interact(plot_missing_data, holeid=Dropdown(options=las_points_df['WellID'].unique(), description='Well ID:'))



Concatenated LAS Points Data:
   AC     CAL  CN  DEN  depth  GR        holeid  PERM  PF  POR  ...      TD  \
0 NaN  16.769 NaN  NaN   40.0 NaN  LONCCARICA-1   NaN NaN  NaN  ...  1764.0   
1 NaN  16.769 NaN  NaN   40.1 NaN  LONCCARICA-1   NaN NaN  NaN  ...  1764.0   
2 NaN  16.769 NaN  NaN   40.2 NaN  LONCCARICA-1   NaN NaN  NaN  ...  1764.0   
3 NaN  16.769 NaN  NaN   40.3 NaN  LONCCARICA-1   NaN NaN  NaN  ...  1764.0   
4 NaN  16.733 NaN  NaN   40.4 NaN  LONCCARICA-1   NaN NaN  NaN  ...  1764.0   

             X            Y          Z  From  \
0  680935.0923  5070578.644  217.01538   0.0   
1  680935.0923  5070578.644  217.01538   0.0   
2  680935.0923  5070578.644  217.01538   0.0   
3  680935.0923  5070578.644  217.01538   0.0   
4  680935.0923  5070578.644  217.01538   0.0   

                               Lithology  Strat_Simplified  \
0  clays, gravel, clayey sands with coal             Lonja   
1  clays, gravel, clayey sands with coal             Lonja   
2  clays, gravel, c

interactive(children=(Dropdown(description='Well ID:', options=('LONCCARICA-1', 'VIROVITICA-1', 'SUHOPOLJE-1',…

<function __main__.plot_missing_data(holeid)>

# 3. Analyse et Visualisation des Données

# 3. Intégration des Données VSP

# 5. Seismic data